In [ ]:
!pip install selenium
!pip install lxml
!pip install langchain playwright openai
!playwright install

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 10.0/10.0 MB 22.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 460.2/460.2 kB 43.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 58.3/58.3 kB 7.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 817.0/817.0 kB 7.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 37.4/37.4 MB 27.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 227.4/227.4 kB 19.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.7/1.7 MB 70.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 252.4/252.4 kB 23.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 63.1/63.1 kB 6.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 75.6/75.6 kB 8.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 49.4/49.4 kB 6.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 77.8/77.8 kB 9.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━

In [ ]:
%%shell

# Add debian buster
cat > /etc/apt/sources.list.d/debian.list <<'EOF'
deb [arch=amd64 signed-by=/usr/share/keyrings/debian-buster.gpg] http://deb.debian.org/debian buster main
deb [arch=amd64 signed-by=/usr/share/keyrings/debian-buster-updates.gpg] http://deb.debian.org/debian buster-updates main
deb [arch=amd64 signed-by=/usr/share/keyrings/debian-security-buster.gpg] http://deb.debian.org/debian-security buster/updates main
EOF

# Add keys
apt-key adv --keyserver keyserver.ubuntu.com --recv-keys DCC9EFBF77E11517
apt-key adv --keyserver keyserver.ubuntu.com --recv-keys 648ACFD622F3D138
apt-key adv --keyserver keyserver.ubuntu.com --recv-keys 112695A0E562B32A

apt-key export 77E11517 | gpg --dearmour -o /usr/share/keyrings/debian-buster.gpg
apt-key export 22F3D138 | gpg --dearmour -o /usr/share/keyrings/debian-buster-updates.gpg
apt-key export E562B32A | gpg --dearmour -o /usr/share/keyrings/debian-security-buster.gpg

# Prefer debian repo for chromium* packages only
# Note the double-blank lines between entries
cat > /etc/apt/preferences.d/chromium.pref << 'EOF'
Package: *
Pin: release a=eoan
Pin-Priority: 500


Package: *
Pin: origin "deb.debian.org"
Pin-Priority: 300


Package: chromium*
Pin: origin "deb.debian.org"
Pin-Priority: 700
EOF
apt-get update
apt install chromium-chromedriver

Executing: /tmp/apt-key-gpghome.WbdKJMqzlF/gpg.1.sh --keyserver keyserver.ubuntu.com --recv-keys DCC9EFBF77E11517
gpg: key DCC9EFBF77E11517: public key "Debian Stable Release Key (10/buster) <debian-release@lists.debian.org>" imported
gpg: Total number processed: 1
gpg:               imported: 1
Executing: /tmp/apt-key-gpghome.kezxEyNiyE/gpg.1.sh --keyserver keyserver.ubuntu.com --recv-keys 648ACFD622F3D138
gpg: key DC30D7C23CBBABEE: public key "Debian Archive Automatic Signing Key (10/buster) <ftpmaster@debian.org>" imported
gpg: Total number processed: 1
gpg:               imported: 1
Executing: /tmp/apt-key-gpghome.dWrOsQe1XM/gpg.1.sh --keyserver keyserver.ubuntu.com --recv-keys 112695A0E562B32A
gpg: key 4DFAB270CAA96DFA: public key "Debian Security Archive Automatic Signing Key (10/buster) <ftpmaster@debian.org>" imported
gpg: Total number processed: 1
gpg:               imported: 1
Get:1 http://deb.debian.org/debian buster InRelease [122 kB]
Get:2 http://security.ubuntu.com/ubuntu

In [ ]:
from selenium import webdriver
from selenium.webdriver.common.keys import Keys
from bs4 import BeautifulSoup
import time
from urllib.parse import urljoin
from selenium.webdriver.common.by import By
import json
import re
from selenium.webdriver.common.by import By
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC
from lxml import etree
from selenium.common.exceptions import TimeoutException
from selenium.common.exceptions import NoSuchElementException
from selenium.common.exceptions import ElementClickInterceptedException
from selenium.common.exceptions import ElementNotInteractableException

In [ ]:
def web_driver():
    options = webdriver.ChromeOptions()
    options.add_argument("--verbose")
    options.add_argument('--no-sandbox')
    options.add_argument('--headless')
    options.add_argument('--disable-gpu')
    options.add_argument("--window-size=1920, 1200")
    options.add_argument('--disable-dev-shm-usage')
    driver = webdriver.Chrome(options=options)
    return driver

In [ ]:
# Scroll to the bottom of the page to load more content
def scroll():
  SCROLL_PAUSE_TIME = 2  # Time to pause between scrolls
  last_height = driver.execute_script("return document.body.scrollHeight")
  while True:
      driver.execute_script("window.scrollTo(0, document.body.scrollHeight);")
      time.sleep(SCROLL_PAUSE_TIME)
      new_height = driver.execute_script("return document.body.scrollHeight")
      if new_height == last_height:
          break
      last_height = new_height

In [ ]:
driver = web_driver()

In [ ]:
#fetch all the links of the products from collection page
driver.get('https://www.jaijaidinbd.com/')
# Wait for the element to appear
wait = WebDriverWait(driver, 10)
time.sleep(3)
scroll()
time.sleep(3)
page_source = driver.page_source
time.sleep(2)

In [ ]:
soup = BeautifulSoup(page_source, 'html.parser')

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


# **Prothom Alo**

In [ ]:
all_links = soup.find_all('a', href=True)
matching_links = [link for link in all_links if link.find_parent('li') and '_1G1J7' in link.find_parent('li').get('class', [])]
#print(all_links)
matching_links

[<a aria-label="সর্বশেষ" href="https://www.prothomalo.com/collection/latest" target="_self">সর্বশেষ</a>,
 <a aria-label="রাজনীতি" href="https://www.prothomalo.com/politics" target="_self">রাজনীতি</a>,
 <a aria-label="বাংলাদেশ" href="https://www.prothomalo.com/bangladesh" target="_self">বাংলাদেশ</a>,
 <a aria-label="অপরাধ" href="https://www.prothomalo.com/bangladesh/crime" target="_self">অপরাধ</a>,
 <a aria-label="বিশ্ব" href="https://www.prothomalo.com/world" target="_self">বিশ্ব</a>,
 <a aria-label="বাণিজ্য" href="https://www.prothomalo.com/business" target="_self">বাণিজ্য</a>,
 <a aria-label="মতামত" href="https://www.prothomalo.com/opinion" target="_self">মতামত</a>,
 <a aria-label="খেলা" href="https://www.prothomalo.com/sports" target="_self">খেলা</a>,
 <a aria-label="বিনোদন" href="https://www.prothomalo.com/entertainment" target="_self">বিনোদন</a>,
 <a aria-label="চাকরি" href="https://www.prothomalo.com/chakri" target="_self">চাকরি</a>,
 <a aria-label="জীবনযাপন" href="https://www.pr

In [ ]:
all_extracted_links = set()

def extract_links(url):
    extracted_links = set()
    driver.get(url)  # Load the URL in the browser
    wait = WebDriverWait(driver, 10)
    time.sleep(3)  # Wait for the page to load

    # Scroll the page to load dynamic content
    scroll()

    # Get the initial page source
    page_source = driver.page_source

    # Parse the initial page content
    soup = BeautifulSoup(page_source, 'html.parser')

    # Find all links within the <div> elements with either class 'stories-set gqNK1' or 'stories-set _9rLDm'
    links_within_div = soup.select('div.stories-set.gqNK1 a[href], div._9rLDm a[href]')


    # Add each unique link to the extracted_links set
    for link in links_within_div:
        extracted_links.add(link['href'])
        # Break if we've reached 1000 unique links
        if len(extracted_links) >= 100:
            break

    while len(extracted_links) < 100:
        load_more_element = driver.find_element(By.CSS_SELECTOR, 'span.load-more-content._7QoIj')
        driver.execute_script("arguments[0].click();", load_more_element)
        time.sleep(3)  # Wait for new content to load
        scroll()

        # Get the updated page source
        page_source = driver.page_source
        soup = BeautifulSoup(page_source, 'html.parser')
        # Find all links within the <div class="stories-set gqNK1"> snippet again
        links_within_div = soup.select('div.stories-set.gqNK1 a[href], div._9rLDm a[href]')
        # Add newly loaded unique links to the extracted_links set
        for link in links_within_div:
            extracted_links.add(link['href'])
            print(len(extracted_links))
            if len(extracted_links) >= 100:
                break

    return extracted_links

# for link in matching_links:
#     url = link['href']
url = "https://www.prothomalo.com/sports"
extracted_links = extract_links(url)
all_extracted_links.update(extracted_links)

#Convert the set to a list before printing
all_extracted_links = list(all_extracted_links)
print(all_extracted_links)
print(len(all_extracted_links))

# Close the web driver
#driver.quit()

In [ ]:
extracted_data = []
visited_links = set()

for href in all_extracted_links:
    if href not in visited_links:
        visited_links.add(href)
        driver.get(href)  # Visit the link
        wait = WebDriverWait(driver, 10)
        time.sleep(3)  # Wait for the page to load
        scroll()
        time.sleep(3)

        page_source = driver.page_source
        soup = BeautifulSoup(page_source, 'html.parser')

        # Extract title and article content
        title_element = soup.find('h1', class_='IiRps')
        if title_element:
            title = title_element.text.strip()
        else:
            title = "Title Not Found"
        paragraphs = soup.find_all('div', class_='story-element-text')
        article = ''
        for p in paragraphs:
            p_tags = p.find_all('p')
            for tag in p_tags:
                article += tag.get_text(strip=True) + ' '
                #print(article)

        extracted_data.append({'link': href, 'summary': title, 'article': article})
        print(len(extracted_data))

        # Break if we've reached 10 unique links
        if len(extracted_data) >= 100:
            break

1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100


# **Manab Zamin**

In [ ]:
all_links = soup.find_all('a', href=True)
#print(all_links)
matching_links = [link for link in all_links if link.find_parent('li') and 'nav-item' in link.find_parent('li').get('class', [])]
matching_links

[<a aria-current="page" class="nav-link active fw-bold" href="category.php?cat=1">অনলাইন</a>,
 <a aria-current="page" class="nav-link active fw-bold text-danger" href="paper.php">আজকের পত্রিকা</a>,
 <a aria-current="page" class="nav-link active fw-bold text-success" href="printversion.php">প্রিন্ট সংস্করণ</a>,
 <a aria-current="page" class="nav-link active fw-bold" href="category.php?cat=4">খেলা</a>,
 <a aria-current="page" class="nav-link active fw-bold" href="category.php?cat=5">বিশ্বজমিন</a>,
 <a aria-current="page" class="nav-link active fw-bold" href="category.php?cat=6">বিনোদন</a>,
 <a aria-current="page" class="nav-link active fw-bold" href="category.php?cat=7">দেশ বিদেশ</a>,
 <a aria-current="page" class="nav-link active fw-bold" href="category.php?cat=8">বাংলারজমিন</a>,
 <a aria-current="page" class="nav-link active fw-bold" href="category.php?cat=9">মত-মতান্তর</a>,
 <a aria-current="page" class="nav-link active fw-bold" href="category.php?cat=10">শিক্ষাঙ্গন</a>,
 <a aria-curr

In [ ]:
all_extracted_links = set()

def extract_links(url):
    extracted_links = set()
    driver.get(url)  # Load the URL in the browser
    wait = WebDriverWait(driver, 10)
    time.sleep(3)  # Wait for the page to load

    # Scroll the page to load dynamic content
    scroll()

    # Get the initial page source
    page_source = driver.page_source

    # Parse the initial page content
    soup = BeautifulSoup(page_source, 'html.parser')

    # Find all links within the <div> elements with either class 'stories-set gqNK1' or 'stories-set _9rLDm'
    links_within_div = soup.select('div.row.gx-5.gy-5.mt-5 a[href], div.row.gx-5.gy-5.my-5 a[href]')
    #print(links_within_div)

    # Add each unique link to the extracted_links set
    for link in links_within_div:
        extracted_links.add(link['href'])
        print(len(extracted_links))
        if len(extracted_links) >= 100:
            break

    return extracted_links

# for link in matching_links:
#     url = link['href']
url = "https://mzamin.com/category.php?cat=24"
extracted_links = extract_links(url)
all_extracted_links.update(extracted_links)

#Convert the set to a list before printing
all_extracted_links = list(all_extracted_links)
print(all_extracted_links)
print(len(all_extracted_links))

# Close the web driver
#driver.quit()

1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
['news.php?news=98119', 'news.php?news=98547', 'news.php?news=98004', 'news.php?news=97822', 'news.php?news=98558', 'news.php?news=98650', 'news.php?news=98928', 'news.php?news=98502', 'news.php?news=98190', 'news.php?news=98123', 'news.php?news=98306', 'news.php?news=98529', 'news.php?news=97829', 'news.php?news=98800', 'news.php?news=97738', 'news.php?news=98377', 'news.php?news=97892', 'news.php?news=98188', 'news.php?news=98511', 'news.php?news=98394', 'news.php?news=98783', 'news.php?news=98501', 'news.php?news=98908', 'news.php?news=97988', 'news.php?news=97757', 'news.php?news=98227', 'news.php?news=98007', 'news.php?news=98045', 'news.php?news=98636', 'news.php?news=98120', 'news.php?news=98639', 'news.php?news=97877', 'news.php?news=98646', 'news.php?news=98248', 'new

In [ ]:
all_extracted_links = ['https://mzamin.com/' + element for element in all_extracted_links]
all_extracted_links

['https://mzamin.com/news.php?news=98119',
 'https://mzamin.com/news.php?news=98547',
 'https://mzamin.com/news.php?news=98004',
 'https://mzamin.com/news.php?news=97822',
 'https://mzamin.com/news.php?news=98558',
 'https://mzamin.com/news.php?news=98650',
 'https://mzamin.com/news.php?news=98928',
 'https://mzamin.com/news.php?news=98502',
 'https://mzamin.com/news.php?news=98190',
 'https://mzamin.com/news.php?news=98123',
 'https://mzamin.com/news.php?news=98306',
 'https://mzamin.com/news.php?news=98529',
 'https://mzamin.com/news.php?news=97829',
 'https://mzamin.com/news.php?news=98800',
 'https://mzamin.com/news.php?news=97738',
 'https://mzamin.com/news.php?news=98377',
 'https://mzamin.com/news.php?news=97892',
 'https://mzamin.com/news.php?news=98188',
 'https://mzamin.com/news.php?news=98511',
 'https://mzamin.com/news.php?news=98394',
 'https://mzamin.com/news.php?news=98783',
 'https://mzamin.com/news.php?news=98501',
 'https://mzamin.com/news.php?news=98908',
 'https://m

In [ ]:
import re
extracted_data = []
visited_links = set()

for href in all_extracted_links:
    if href not in visited_links:
        visited_links.add(href)
        driver.get(href)  # Visit the link
        wait = WebDriverWait(driver, 10)
        time.sleep(3)  # Wait for the page to load
        scroll()
        time.sleep(3)

        page_source = driver.page_source
        soup = BeautifulSoup(page_source, 'html.parser')

        # Extract title and article content
        title_element = soup.find('h1', class_='lh-base fs-1')
        if title_element:
            title = title_element.text.strip()
        else:
            title = "Title Not Found"

        paragraphs = soup.find_all('div', class_='col-sm-10 offset-sm-1 fs-5 lh-base mt-4 mb-5')
        article = ''
        bengali_pattern = re.compile(r'[\u0980-\u09FF\s,.।!?\'":;(){}\[\]‘’\-]+')
        for p in paragraphs:
            p_tags = p.find_all('p')
            for tag in p_tags:
                p_text = tag.get_text(strip=True)
                bengali_text = ''.join(re.findall(bengali_pattern, p_text))
                bengali_text = re.sub(r'\s+', ' ', bengali_text)
                article += bengali_text + ' '
            print(article)

        extracted_data.append({'link': href, 'summary': title, 'article': article})
        print(len(extracted_data))

        # Break if we've reached 10 unique links
        if len(extracted_data) >= 100:
            break

বাংলাদেশ এখন বহুমুখী সংকটে পতিত বলে মন্তব্য করেছেন গণঅধিকার পরিষদের সভাপতি নুরুল হক নুর। শুক্রবার জাতীয় প্রেসক্লাবের গণঅধিকার পরিষদের উদ্যোগে ‘গণতন্ত্র-ভোটাধিকার ,স্বাধীনতা-সার্বভৌমত্ব রক্ষায় ভিন দেশী আধিপত্য ও আগ্রাসন বিরোধী’ বিক্ষোভ মিছিলপূর্ব সমাবেশে এ মন্তব্য করেন তিনি। সমাবেশ শেষে প্রেসক্লাবের সামনে থেকে মিছিল বের করেন নেতাকর্মীরা। তাদের মিছিলটি পল্টন মোড়, ফকিরাপুল, বিএনপির কেন্দ্রীয় কার্যালয়, নাইটিংগেল মোড় ঘুরে বিজয়নগর পানির ট্যাংকির সামনে গিয়ে শেষ হয়।  .  . .  . নুরুল হক নুর বলেন, বাংলাদেশ এখন বহুমুখী সংকটে পতিত। একদিকে দীর্ঘদিনের ভারতীয় আগ্রাসন। এদেশে কারা সরকারে থাকবে, বিরোধী দল কারা হবে। কে এমপি, মন্ত্রী হবে, কে প্রশাসনের শীর্ষ পদে নিয়োগ পাবে, তা ঠিক করে দেয় ভারত। আজ সর্বত্র ভারতীয় আধিপত্য। ভারতীয় আগ্রাসন থেকে দেশকে রক্ষায় ভারতীয় পণ্য বর্জনের যে আন্দোলন চলছে, তা শহর থেকে গ্রাম, পাড়া-মহল্লা সর্বত্র ছড়িয়ে দিতে হবে। তিনি বলেন, বাংলাদেশে থাকা ভারতীয় এজেন্টদের চিহ্নিত করতে হবে। এ দেশে ১০ লাখের বেশি অবৈধ ভারতীয় লোক রয়েছে, তাদেরকে চিহ্নিত করতে হবে।  গণঅধিকার পরিষদের যুগ্ম সাধারণ সম্

# **Kaler Kantho**

In [ ]:
specific_element = soup.find('ul', class_='nav nav-pills nav-fill')
matching_links = specific_element.find_all('a')

# Print the extracted <a> tags
for a_tag in matching_links:
    print(a_tag)

<a aria-expanded="false" class="nav-link dropdown-toggle" data-bs-toggle="dropdown" href="#" role="button">বাংলাদেশ</a>
<a class="dropdown-item" href="/online/country-news">সারাবাংলা</a>
<a class="dropdown-item" href="/online/national">জাতীয়</a>
<a class="dropdown-item" href="/online/campus-online">শিক্ষা</a>
<a class="dropdown-item" href="/online/Politics">রাজনীতি</a>
<a class="nav-link" href="/online/world">বিশ্ব</a>
<a class="nav-link" href="/online/sport">খেলা</a>
<a class="nav-link" href="/online/entertainment">বিনোদন</a>
<a class="nav-link" href="/online/business">বাণিজ্য</a>
<a aria-expanded="false" class="nav-link dropdown-toggle" data-bs-toggle="dropdown" href="#" role="button">ইসলামী জীবন</a>
<a class="dropdown-item" href="/online/Islamic-lifestylie">অনলাইন</a>
<a class="dropdown-item" href="/print-edition/islamic-life">প্রিন্ট</a>
<a class="nav-link" href="/online/lifestyle">জীবনযাপন</a>
<a class="nav-link" href="/online/shuvosangho">বসুন্ধরা শুভসংঘ</a>
<a class="nav-link t

In [ ]:
all_extracted_links = set()

def extract_links(url):
    extracted_links = set()
    driver.get(url)  # Load the URL in the browser
    wait = WebDriverWait(driver, 10)
    time.sleep(3)  # Wait for the page to load

    # Scroll the page to load dynamic content
    scroll()

    # Get the initial page source
    page_source = driver.page_source

    # Parse the initial page content
    soup = BeautifulSoup(page_source, 'html.parser')

    # Find all links within the <div> elements with either class 'stories-set gqNK1' or 'stories-set _9rLDm'
    links_within_div = soup.select('div.col-12.col-md-12.col-lg-8.col-xl-8 a.row.mb-4[href]')
    #print(links_within_div)

    # Add each unique link to the extracted_links set
    for link in links_within_div:
        extracted_links.add(link['href'])
        # Break if we've reached 1000 unique links
        if len(extracted_links) >= 200:
            break

    while len(extracted_links) < 200:
      try:
        load_more_element = driver.find_element(By.CSS_SELECTOR, 'div.col-3.col-md-2 button.btn.btn-outline-success')
        #driver.execute_script("arguments[0].click();", load_more_element)
        load_more_element.click()
        time.sleep(3)  # Wait for new content to load
        scroll()

        # Get the updated page source
        page_source = driver.page_source
        soup = BeautifulSoup(page_source, 'html.parser')
        # Find all links within the <div class="stories-set gqNK1"> snippet again
        links_within_div = soup.select('div.col-12.col-md-12.col-lg-8.col-xl-8 a.row.mb-4[href]')
        #print(links_within_div)
        # Add newly loaded unique links to the extracted_links set
        for link in links_within_div:
            extracted_links.add(link['href'])
            #print(len(extracted_links))
            if len(extracted_links) >= 200:
                break
      except NoSuchElementException:
          print("No more load_more_element found. Exiting loop.")
          break

    return extracted_links

# for link in matching_links:
#     url = link['href']
url = "https://www.kalerkantho.com/feature/rongermela"
extracted_links = extract_links(url)
all_extracted_links.update(extracted_links)

#Convert the set to a list before printing
all_extracted_links = list(all_extracted_links)
print(all_extracted_links)
print(len(all_extracted_links))

# Close the web driver
#driver.quit()

No more load_more_element found. Exiting loop.
['/feature/rongermela/2023/11/23/1338810', '/feature/rongermela/2023/06/22/1292256', '/feature/rongermela/2023/03/23/1263740', '/feature/rongermela/2023/07/20/1300330', '/feature/rongermela/2023/06/08/1287687', '/feature/rongermela/2023/08/03/1304736', '/feature/rongermela/2023/12/21/1347527', '/feature/rongermela/2023/09/07/1315658', '/feature/rongermela/2023/08/31/1313555', '/feature/rongermela/2023/09/21/1319989', '/feature/rongermela/2023/10/26/1330239', '/feature/rongermela/2023/07/20/1300316', '/feature/rongermela/2023/09/28/1321993', '/feature/rongermela/2023/07/13/1298007', '/feature/rongermela/2023/06/01/1285512', '/feature/rongermela/2023/03/30/1265993', '/feature/rongermela/2023/06/22/1292250', '/feature/rongermela/2023/03/16/1261511', '/feature/rongermela/2023/07/27/1302580', '/feature/rongermela/2023/11/16/1336539', '/feature/rongermela/2024/02/08/1361664', '/feature/rongermela/2023/02/02/1241130', '/feature/rongermela/2023/12

In [ ]:
all_extracted_links = ['https://www.kalerkantho.com' + element for element in all_extracted_links]
all_extracted_links

['https://www.kalerkantho.com/feature/rongermela/2023/11/23/1338810',
 'https://www.kalerkantho.com/feature/rongermela/2023/06/22/1292256',
 'https://www.kalerkantho.com/feature/rongermela/2023/03/23/1263740',
 'https://www.kalerkantho.com/feature/rongermela/2023/07/20/1300330',
 'https://www.kalerkantho.com/feature/rongermela/2023/06/08/1287687',
 'https://www.kalerkantho.com/feature/rongermela/2023/08/03/1304736',
 'https://www.kalerkantho.com/feature/rongermela/2023/12/21/1347527',
 'https://www.kalerkantho.com/feature/rongermela/2023/09/07/1315658',
 'https://www.kalerkantho.com/feature/rongermela/2023/08/31/1313555',
 'https://www.kalerkantho.com/feature/rongermela/2023/09/21/1319989',
 'https://www.kalerkantho.com/feature/rongermela/2023/10/26/1330239',
 'https://www.kalerkantho.com/feature/rongermela/2023/07/20/1300316',
 'https://www.kalerkantho.com/feature/rongermela/2023/09/28/1321993',
 'https://www.kalerkantho.com/feature/rongermela/2023/07/13/1298007',
 'https://www.kalerk

In [ ]:
import re
extracted_data = []
visited_links = set()

for href in all_extracted_links:
    if href not in visited_links:
        visited_links.add(href)
        driver.get(href)  # Visit the link
        wait = WebDriverWait(driver, 10)
        time.sleep(3)  # Wait for the page to load
        scroll()
        time.sleep(3)

        page_source = driver.page_source
        soup = BeautifulSoup(page_source, 'html.parser')

        # Extract title and article content
        title_element = soup.find('h1', class_='my-3')
        if title_element:
            title = title_element.text.strip()
            print('Title: ',title)
        else:
            title = "Title Not Found"

        article = ''
        current_tag = soup.find(['article', 'div'], class_=['mb-5', 'my-5'])
        while current_tag:
            if 'newsGoogle' in current_tag.get('class', []):
                break
            elif 'mb-5' in current_tag.get('class', []) or 'my-5' in current_tag.get('class', []):
                article += current_tag.get_text(strip=True) + ' '
            # Move to the next sibling
            current_tag = current_tag.find_next(['article', 'div'], class_=['mb-5', 'my-5', 'newsGoogle'])
        print(article)

        extracted_data.append({'link': href, 'summary': title, 'article': article})
        print(len(extracted_data))

        # Break if we've reached 10 unique links
        if len(extracted_data) >= 200:
            break

Title:  শুভ জন্মদিন
এ সপ্তাহে যাঁদের জন্মদিন [২৩—২৯ নভেম্বর]মিশু চৌধুরী,উজ্জল মাহমুদ [২৪ নভেম্বর]শ্রাবস্তী দত্ত তিন্নি,প্রিয়া ডায়েস[২৫ নভেম্বর]ইভান মনোয়ার [২৬ নভেম্বর]ফারজানা চুমকি,জাহিদুর রহিম অঞ্জন,সাজেদ ফাতেমী[২৭ নভেম্বর]দীপা খন্দকার,কাজী জেসিন,আবু হায়াত মাহমুদ[২৮ নভেম্বর]এফ এস নাঈম,মিজানুর রহমান আরিয়ান,জ্যোতি সিনহা[২৯ নভেম্বর]। 
1
Title:  শুভ জন্মদিন
শাফায়েত মনসুর রানা [২২ জুন]নেহাল কোরাইশি [২৪ জুন]সাবরিন সাকা মীম, সিদ্দিকুর রহমান, সৈয়দ বাবু [২৫ জুন]আশুতোষ সুজন [২৬ জুন]অঞ্জনা সুলতানা, জিয়াউল ফারুক অপূর্ব, জায়ান ফারুক আয়াশ [২৭ জুন]। 
2
Title:  স্টার অব দ্য উইক
ডিজিটাল নিরাপত্তা আইনে‘অগ্নি’অভিনেত্রীর বিরুদ্ধে মামলা হলো শুক্রবার রাতে, পরদিন দুপুরেই বিমানবন্দর থেকে তাঁকে গ্রেপ্তার, সেদিন বিকেলেই মিলল জামিন। গ্রেপ্তার ও জামিনের মধ্যবর্তী সময়ে সামাজিক যোগাযোগ মাধ্যমে রীতিমতো প্রতিবাদের ঝড় বয়ে গেল। ৯ মাসের অন্তঃসত্ত্বা মাহিকে নিয়ে উদ্বিগ্ন হয়ে ওঠেন অনেকেই।। 
3
Title:  স্টার অব দ্য উইক : শাকিব খান
ঈদের ছবি ‘প্রিয়তমা’ এখনো আলোচনায়। তবে এ সপ্তাহে ফের আলোচনায় অভিনেতার ব্যক্তিজীবন। আমেরিকার রা

# **Ittefaq**

In [ ]:
specific_element = soup.find('div', class_='main_menu')
matching_links = specific_element.find_all('a')

# Print the extracted <a> tags
for a_tag in matching_links:
    print(a_tag)

<a class="static" href="//www.ittefaq.com.bd/latest-news">সর্বশেষ</a>
<a class="" href="https://www.ittefaq.com.bd/topic/%E0%A6%AC%E0%A6%BF%E0%A6%B6%E0%A7%87%E0%A6%B7-%E0%A6%B8%E0%A6%82%E0%A6%AC%E0%A6%BE%E0%A6%A6">বিশেষ সংবাদ</a>
<a class="dynamic" href="//www.ittefaq.com.bd/national">জাতীয়</a>
<a class="dynamic" href="//www.ittefaq.com.bd/country">সারাদেশ</a>
<a class="dynamic" href="//www.ittefaq.com.bd/politics">রাজনীতি</a>
<a class="dynamic" href="//www.ittefaq.com.bd/world-news">বিশ্ব সংবাদ</a>
<a class="dynamic" href="//www.ittefaq.com.bd/sports">খেলা</a>
<a class="dynamic" href="//www.ittefaq.com.bd/entertainment">বিনোদন</a>
<a class="dynamic" href="//www.ittefaq.com.bd/business">বাণিজ্য</a>
<a class="dynamic" href="//www.ittefaq.com.bd/lifestyle">লাইফস্টাইল</a>
<a class="dynamic" href="//www.ittefaq.com.bd/tech">টেক</a>
<a class="dynamic" href="//www.ittefaq.com.bd/offbeat">ভিন্নচোখে</a>
<a class="dynamic" href="//www.ittefaq.com.bd/video">ভিডিও</a>
<a class="dynamic" href="//w

In [ ]:
all_extracted_links = set()

def extract_links(url):
    extracted_links = set()
    driver.get(url)  # Load the URL in the browser
    wait = WebDriverWait(driver, 10)
    time.sleep(3)  # Wait for the page to load

    # Scroll the page to load dynamic content
    scroll()

    # Get the initial page source
    page_source = driver.page_source

    # Parse the initial page content
    soup = BeautifulSoup(page_source, 'html.parser')

    # Find all links within the <div> elements with either class 'stories-set gqNK1' or 'stories-set _9rLDm'
    links_within_div = soup.select('div.row div.col.col1 h2.title a.link_overlay[href]')
    #print(links_within_div)

    # Add each unique link to the extracted_links set
    for link in links_within_div:
        extracted_links.add(link['href'])
        # Break if we've reached 1000 unique links
        if len(extracted_links) >= 400:
            break

    while len(extracted_links) < 400:
      try:
        load_more_element = driver.find_element(By.CSS_SELECTOR, 'div.load_more_status button.ajax_load_btn')
        driver.execute_script("arguments[0].click();", load_more_element)
        #load_more_element.click()
        time.sleep(3)  # Wait for new content to load
        scroll()

        # Get the updated page source
        page_source = driver.page_source
        soup = BeautifulSoup(page_source, 'html.parser')
        # Find all links within the <div class="stories-set gqNK1"> snippet again
        links_within_div = soup.select('div.row div.col.col1 h2.title a.link_overlay[href]')
        #print(links_within_div)
        # Add newly loaded unique links to the extracted_links set
        for link in links_within_div:
            extracted_links.add(link['href'])
            #print(len(extracted_links))
            if len(extracted_links) >= 400:
                break
      except NoSuchElementException:
          print("No more load_more_element found. Exiting loop.")
          break

    return extracted_links

# for link in matching_links:
#     url = link['href']
url = "http://www.ittefaq.com.bd/lifestyle"
extracted_links = extract_links(url)
all_extracted_links.update(extracted_links)

#Convert the set to a list before printing
all_extracted_links = list(all_extracted_links)
print(all_extracted_links)
print(len(all_extracted_links))

# Close the web driver
#driver.quit()

['//www.ittefaq.com.bd/666262/%E0%A6%B8%E0%A6%95%E0%A6%BE%E0%A6%B2%E0%A7%87%E0%A6%B0-%E0%A6%A8%E0%A6%BE%E0%A6%B6%E0%A6%A4%E0%A6%BE%E0%A7%9F-%E0%A6%93%E0%A6%9F%E0%A6%B8', '//www.ittefaq.com.bd/669489/%E0%A6%B6%E0%A7%80%E0%A6%A4%E0%A7%87%E0%A6%B0-%E0%A6%B6%E0%A7%81%E0%A6%B0%E0%A7%81%E0%A6%A4%E0%A7%87-%E0%A6%86%E0%A6%9A%E0%A6%AE%E0%A6%95%E0%A6%BE-%E0%A6%AC%E0%A7%83%E0%A6%B7%E0%A7%8D%E0%A6%9F%E0%A6%BF-%E0%A6%B8%E0%A7%81%E0%A6%B8%E0%A7%8D%E0%A6%A5-%E0%A6%A5%E0%A6%BE%E0%A6%95%E0%A6%A4%E0%A7%87-%E0%A6%95%E0%A6%B0%E0%A6%A3%E0%A7%80%E0%A7%9F', '//www.ittefaq.com.bd/669377/%E0%A6%AC%E0%A6%BE%E0%A7%9C%E0%A6%BF%E0%A6%A4%E0%A7%87%E0%A6%87-%E0%A6%AC%E0%A6%BE%E0%A6%A8%E0%A6%BE%E0%A6%A8-%E0%A6%A1%E0%A7%8D%E0%A6%B0%E0%A6%BE%E0%A6%87-%E0%A6%AB%E0%A7%8D%E0%A6%B0%E0%A7%82%E0%A6%9F%E0%A6%B8', '//www.ittefaq.com.bd/663361/%E0%A6%9C%E0%A6%B2%E0%A6%AA%E0%A6%BE%E0%A6%87-%E0%A6%B8%E0%A6%82%E0%A6%B0%E0%A6%95%E0%A7%8D%E0%A6%B7%E0%A6%A3%E0%A7%87%E0%A6%B0-%E0%A6%AA%E0%A6%A6%E0%A7%8D%E0%A6%A7%E0%A6%A4%E0%A6%BF', '//

In [ ]:
all_extracted_links = ['https:' + element for element in all_extracted_links]
all_extracted_links

['https://www.ittefaq.com.bd/666262/%E0%A6%B8%E0%A6%95%E0%A6%BE%E0%A6%B2%E0%A7%87%E0%A6%B0-%E0%A6%A8%E0%A6%BE%E0%A6%B6%E0%A6%A4%E0%A6%BE%E0%A7%9F-%E0%A6%93%E0%A6%9F%E0%A6%B8',
 'https://www.ittefaq.com.bd/669489/%E0%A6%B6%E0%A7%80%E0%A6%A4%E0%A7%87%E0%A6%B0-%E0%A6%B6%E0%A7%81%E0%A6%B0%E0%A7%81%E0%A6%A4%E0%A7%87-%E0%A6%86%E0%A6%9A%E0%A6%AE%E0%A6%95%E0%A6%BE-%E0%A6%AC%E0%A7%83%E0%A6%B7%E0%A7%8D%E0%A6%9F%E0%A6%BF-%E0%A6%B8%E0%A7%81%E0%A6%B8%E0%A7%8D%E0%A6%A5-%E0%A6%A5%E0%A6%BE%E0%A6%95%E0%A6%A4%E0%A7%87-%E0%A6%95%E0%A6%B0%E0%A6%A3%E0%A7%80%E0%A7%9F',
 'https://www.ittefaq.com.bd/669377/%E0%A6%AC%E0%A6%BE%E0%A7%9C%E0%A6%BF%E0%A6%A4%E0%A7%87%E0%A6%87-%E0%A6%AC%E0%A6%BE%E0%A6%A8%E0%A6%BE%E0%A6%A8-%E0%A6%A1%E0%A7%8D%E0%A6%B0%E0%A6%BE%E0%A6%87-%E0%A6%AB%E0%A7%8D%E0%A6%B0%E0%A7%82%E0%A6%9F%E0%A6%B8',
 'https://www.ittefaq.com.bd/663361/%E0%A6%9C%E0%A6%B2%E0%A6%AA%E0%A6%BE%E0%A6%87-%E0%A6%B8%E0%A6%82%E0%A6%B0%E0%A6%95%E0%A7%8D%E0%A6%B7%E0%A6%A3%E0%A7%87%E0%A6%B0-%E0%A6%AA%E0%A6%A6%E0%A7%8D%E0%A6

In [ ]:
import re
extracted_data = []
visited_links = set()

for href in all_extracted_links:
    if href not in visited_links:
        visited_links.add(href)
        driver.get(href)  # Visit the link
        wait = WebDriverWait(driver, 10)
        time.sleep(3)  # Wait for the page to load
        scroll()
        time.sleep(3)

        page_source = driver.page_source
        soup = BeautifulSoup(page_source, 'html.parser')

        # Extract title and article content
        title_element = soup.find('h1', class_='title mb10')
        if title_element:
            title = title_element.text.strip()
            print('Title: ',title)
        else:
            title = "Title Not Found"

        paragraphs = soup.find_all('div', class_='viewport jw_article_body')
        article = ''
        for p in paragraphs:
            p_tags = p.find_all('p', class_='alignfull')
            for tag in p_tags:
                article += tag.get_text(strip=True) + ' '
        print(article)

        extracted_data.append({'link': href, 'summary': title, 'article': article})
        print(len(extracted_data))

        # Break if we've reached 10 unique links
        if len(extracted_data) >= 400:
            break

Title:  সকালের নাশতায় ওটস
সকালে নাশতায় ওটস এখন বেশ জনপ্রিয়। স্বাস্থ্যসচেতনরা অধিকাংশ ক্ষেত্রেই তারা ওজনের কথা ভেবে ওটস খেয়ে থাকেন। তবে ওটসের মূল কাজ ওজন কমানোই নয়। আরও কিছু স্বাস্থ্য উপকারিতা রয়েছে। সেগুলো একবার দেখে নেওয়া যাক: পুষ্টি উপাদানওটসের পুষ্টির গঠন বেশ সুষম। এটি কার্বোহাইড্রেট ও ফাইবারের খুব ভালো একটি উৎস। অন্যান্য খাদ্যশস্যের তুলনায় এতে আছে অনেক বেশি প্রোটিন ও ফ্যাট। আধ কাপ (৭৮ গ্রাম) ওটসে আছে দৈনন্দিন চাহিদার ১৯১ শতাংশ ম্যাংগানিজ, ৪১ শতাংশ ফসফরাস, ৩৪ শতাংশ ম্যাগনেশিয়াম, ২৪ শতাংশ কপার, ২০ শতাংশ আয়রন, ২০ শতাংশ জিঙ্ক, ১১ শতাংশ ফোলেট, ৩৯ শতাংশ ভিটামিন বি-১ (থায়ামিন), ১০ শতাংশ ভিটামিন বি-৫ (প্যান্টোথেনিক অ্যাসিড)। এ ছাড়া আছে ৫১ গ্রাম কার্বোহাইড্রেট, ১৩ গ্রাম প্রোটিন, ৫ গ্রাম ফ্যাট, ৮ গ্রাম ফাইবার এবং সামান্য কিছু ক্যালসিয়াম, পটাশিয়াম, ভিটামিন বি-৬ (পিরিডক্সিন), ভিটামিন বি-৩ (নায়াসিন)। এত কিছুর পরও ক্যালরি মাত্র ৩০৩। ওজন কমাতে সহায়কওটস খেলে অনেকক্ষণ পেট ভরা থাকে। তাই দিনে হুটহাট খিদে পায় না। কারণ ওটসে থাকা গ্লুকোন ও পেপটাইডের বন্ধন। এই দুই উপাদান হলো ক্ষুধা নিয়ন্ত্রণকারী হরমোন। ক

# **Bangladesh Protidin**

In [ ]:
#all_links = soup.find_all('a', href=True)
# all_links
specific_element = soup.find('ul', class_='navbar-nav')
matching_links = specific_element.find_all('a',class_=['nav-link','dropdown-item'])

# Print the extracted <a> tags
for a_tag in matching_links:
    print(a_tag)

<a class="nav-link" href="https://www.bd-pratidin.com/"><i class="text-secondary bi bi-house-fill"></i></a>
<a class="nav-link" href="national">জাতীয়</a>
<a class="nav-link" href="country">দেশগ্রাম</a>
<a class="nav-link" href="entertainment">শোবিজ</a>
<a class="nav-link" href="international-news">পূর্ব-পশ্চিম</a>
<a class="nav-link" href="islam">ইসলামী জীবন</a>
<a class="nav-link dropdown-toggle" data-bs-toggle="dropdown" href="#"> অন্যান্য </a>
<a class="dropdown-item" href="economy">শিল্প বাণিজ্য</a>
<a class="dropdown-item" href="campus-online">ক্যাম্পাস</a>
<a class="dropdown-item" href="corporate-corner">কর্পোরেট কর্নার</a>
<a class="dropdown-item" href="health-tips">হেলথ কর্নার</a>
<a class="dropdown-item" href="life">জীবন ধারা</a>
<a class="dropdown-item" href="open-air-theater">মুক্তমঞ্চ</a>
<a class="dropdown-item" href="mixter">পাঁচফোড়ন</a>
<a class="dropdown-item" href="sports">মাঠে ময়দানে</a>
<a class="dropdown-item" href="city-news">নগর জীবন</a>
<a class="dropdown-item" 

In [ ]:
all_extracted_links = set()

def extract_links(url):
    extracted_links = set()
    driver.get(url)  # Load the URL in the browser
    wait = WebDriverWait(driver, 10)
    time.sleep(3)  # Wait for the page to load

    # Scroll the page to load dynamic content
    scroll()

    # Get the initial page source
    page_source = driver.page_source

    # Parse the initial page content
    soup = BeautifulSoup(page_source, 'html.parser')

    # Find all links within the <div> elements with either class 'stories-set gqNK1' or 'stories-set _9rLDm'
    links_within_div = soup.select('div.row div.col-md-6.mt-4 div.cat-2nd-lead a.row[href], div.row div.col-md-3.mt-4 a.list-item[href]')
    #print(links_within_div)

    # Add each unique link to the extracted_links set
    for link in links_within_div:
        extracted_links.add(link['href'])
        # Break if we've reached 1000 unique links
        if len(extracted_links) >= 400:
            break

    while len(extracted_links) < 400:
      try:
        link_element = driver.find_element(By.CSS_SELECTOR, 'div.col-md-12.text-end a.btn.btn-success[href]')

        # Click on the anchor element
        link_element.click()
        #load_more_element.click()
        time.sleep(3)  # Wait for new content to load
        scroll()

        # Get the updated page source
        page_source = driver.page_source
        soup = BeautifulSoup(page_source, 'html.parser')
        # Find all links within the <div class="stories-set gqNK1"> snippet again
        links_within_div = soup.select('div.row div.col-md-6.mt-4 div.cat-2nd-lead a.row[href], div.row div.col-md-3.mt-4 a.list-item[href]')
        #print(links_within_div)
        # Add newly loaded unique links to the extracted_links set
        for link in links_within_div:
            extracted_links.add(link['href'])
            #print(len(extracted_links))
            if len(extracted_links) >= 400:
                break
      except NoSuchElementException:
          print("No more load_more_element found. Exiting loop.")
          break

    return extracted_links

# for link in matching_links:
#     url = link['href']
url = "https://www.bd-pratidin.com/chittagong-pratidin"
extracted_links = extract_links(url)
all_extracted_links.update(extracted_links)

#Convert the set to a list before printing
all_extracted_links = list(all_extracted_links)
print(all_extracted_links)
print(len(all_extracted_links))

# Close the web driver
#driver.quit()

No more load_more_element found. Exiting loop.
['chittagong-pratidin/2024/02/28/971775', 'chittagong-pratidin/2024/02/27/971579', 'chittagong-pratidin/2024/02/28/971798', 'chittagong-pratidin/2024/02/28/971800', 'chittagong-pratidin/2024/02/28/971824', 'chittagong-pratidin/2024/02/24/970793', 'chittagong-pratidin/2024/02/28/971802', 'chittagong-pratidin/2024/02/26/971180', 'chittagong-pratidin/2024/02/24/970836', 'chittagong-pratidin/2024/02/27/971525', 'chittagong-pratidin/2024/02/24/970784', 'chittagong-pratidin/2024/02/27/971490', 'chittagong-pratidin/2024/02/24/970829', 'chittagong-pratidin/2024/02/28/971774', 'chittagong-pratidin/2024/02/27/971568', 'chittagong-pratidin/2024/02/26/971216', 'chittagong-pratidin/2024/02/26/971200', 'chittagong-pratidin/2024/02/26/971234', 'chittagong-pratidin/2024/02/24/970770', 'chittagong-pratidin/2024/02/26/971211', 'chittagong-pratidin/2024/02/29/972060', 'chittagong-pratidin/2024/02/24/970778', 'chittagong-pratidin/2024/02/24/970766', 'chittago

In [ ]:
all_extracted_links = ['https://www.bd-pratidin.com/' + element for element in all_extracted_links]
all_extracted_links

['https://www.bd-pratidin.com/chittagong-pratidin/2024/02/28/971775',
 'https://www.bd-pratidin.com/chittagong-pratidin/2024/02/27/971579',
 'https://www.bd-pratidin.com/chittagong-pratidin/2024/02/28/971798',
 'https://www.bd-pratidin.com/chittagong-pratidin/2024/02/28/971800',
 'https://www.bd-pratidin.com/chittagong-pratidin/2024/02/28/971824',
 'https://www.bd-pratidin.com/chittagong-pratidin/2024/02/24/970793',
 'https://www.bd-pratidin.com/chittagong-pratidin/2024/02/28/971802',
 'https://www.bd-pratidin.com/chittagong-pratidin/2024/02/26/971180',
 'https://www.bd-pratidin.com/chittagong-pratidin/2024/02/24/970836',
 'https://www.bd-pratidin.com/chittagong-pratidin/2024/02/27/971525',
 'https://www.bd-pratidin.com/chittagong-pratidin/2024/02/24/970784',
 'https://www.bd-pratidin.com/chittagong-pratidin/2024/02/27/971490',
 'https://www.bd-pratidin.com/chittagong-pratidin/2024/02/24/970829',
 'https://www.bd-pratidin.com/chittagong-pratidin/2024/02/28/971774',
 'https://www.bd-pra

In [ ]:
import re
extracted_data = []
visited_links = set()

for href in all_extracted_links:
    if href not in visited_links:
        visited_links.add(href)
        driver.get(href)  # Visit the link
        wait = WebDriverWait(driver, 10)
        time.sleep(3)  # Wait for the page to load
        scroll()
        time.sleep(3)

        page_source = driver.page_source
        soup = BeautifulSoup(page_source, 'html.parser')

        # Extract title and article content
        title_element = soup.find('h1', class_='ps-3 pe-1')
        if title_element:
            title = title_element.text.strip()
            print('Title: ',title)
        else:
            title = "Title Not Found"

        paragraphs = soup.find_all('article', class_='mt-3')
        article = ''
        for p in paragraphs:
            p_tags = p.find_all('p')
            for tag in p_tags:
                article += tag.get_text(strip=True) + ' '
        print(article)

        extracted_data.append({'link': href, 'summary': title, 'article': article})
        print(len(extracted_data))

        # Break if we've reached 10 unique links
        if len(extracted_data) >= 400:
            break

Title:  ৬৬ কিমি সড়কে এলইডি বাতি স্থাপন করবে চসিক
চট্টগ্রাম সিটি কর্পোরেশন (চসিক) নগরজুড়ে ৬৬ কিলোমিটার সড়কে এলইডি বাতি স্থাপনের কাজের উদ্বোধন করেছেন চসিক মেয়র বীর মুক্তিযোদ্ধা মো. রেজাউল করিম চৌধুরী। বুধবার বিকালে কোর্ট বিল্ডিংস্থ শহীদ মিনার প্রাঙ্গণে কোভিড-১৯ রিকভারি প্রজেক্টের আওতায় প্রথম পর্যায়ে নগরীর ৬৬ কিমি রাস্তায় এলইডি বাতি স্থাপনের কাজের উদ্বোধন করেন মেয়র। মেয়র বলেন, আমি পুরো নগরীকে আলোকায়নের উদ্যোগ গ্রহণ করেছি। প্রাথমিকভাবে আজ ৬৬ কিমি রাস্তায় এলইডি বাতি স্থাপনের কাজ শুরু হল। পর্যায়ক্রমে পুরো নগরীকে আলোকায়ন করা হবে। এছাড়া আলোকায়নে গুরুত্ব দেয়া হচ্ছে নান্দনিকতায়ও। প্রজাপতি ও নৌকার আদলে বাতি দিয়ে শহরের রাতের সৌন্দর্যে ভিন্ন মাত্রা যোগ করা হচ্ছে।  মেয়র বলেন, ফুটপাত রক্ষায় চসিক অনড়। অবৈধভাবে ফুটপাত দখলকারীদের জনস্বার্থে উচ্ছেদ করেছি। অবৈধভাবে রাস্তা দখলের জন্য চাপ তৈরি করতে একটি মহল আন্দোলনের হুমকি দিচ্ছে। কার আন্দোলন? কীসের আন্দোলন? জনগণের ফুটপাত দখল করার অধিকার ওদের কে দিয়েছে? যত আন্দোলনই করেননা কেন আমি ফুটপাতে অবৈধভাবে বসতে দিবনা। এসময় উপস্থিত ছিলেন চসিকের প্রধান নির্বাহী কর্মকর

# **Janakantha**

In [ ]:
#all_links = soup.find_all('a', href=True)
# all_links
specific_element = soup.find('ul', class_='navbar-nav m-auto')
matching_links = specific_element.find_all('a')

# Print the extracted <a> tags
for a_tag in matching_links:
    print(a_tag)

<a class="nav-link" href="https://www.dailyjanakantha.com/latest-news/">সর্বশেষ</a>
<a aria-expanded="false" class="nav-link dropdown-toggle" data-bs-toggle="dropdown disable" href="https://www.dailyjanakantha.com/national/" id="navbarDropdown" role="button">জাতীয় <i class="fa fa-angle-down"></i></a>
<a class="dropdown-item" href="https://www.dailyjanakantha.com/national/capital">রাজধানী</a>
<a class="nav-link" href="https://www.dailyjanakantha.com/politics/">রাজনীতি</a>
<a aria-expanded="false" class="nav-link dropdown-toggle" data-bs-toggle="dropdown disable" href="https://www.dailyjanakantha.com/bangladesh/" id="navbarDropdown" role="button">বাংলাদেশ <i class="fa fa-angle-down"></i></a>
<a class="dropdown-item" href="https://www.dailyjanakantha.com/divisions/dhaka/">ঢাকা</a>
<a class="dropdown-item" href="https://www.dailyjanakantha.com/divisions/chattogram/">চট্টগ্রাম</a>
<a class="dropdown-item" href="https://www.dailyjanakantha.com/divisions/rajshahi/">রাজশাহী</a>
<a class="dropd

In [ ]:
all_extracted_links = set()

def extract_links(url):
    extracted_links = set()
    driver.get(url)  # Load the URL in the browser
    wait = WebDriverWait(driver, 10)
    time.sleep(3)  # Wait for the page to load

    # Scroll the page to load dynamic content
    scroll()

    # Get the initial page source
    page_source = driver.page_source

    # Parse the initial page content
    soup = BeautifulSoup(page_source, 'html.parser')

    # Find all links within the <div> elements with either class 'stories-set gqNK1' or 'stories-set _9rLDm'
    links_within_div = soup.select('div.row.read-more-container div.col-lg-12.col-12.countclass div.DCatNewsList3 a[href]')
    #print(links_within_div)

    # Add each unique link to the extracted_links set
    for link in links_within_div:
        extracted_links.add(link['href'])
        # Break if we've reached 1000 unique links
        if len(extracted_links) >= 400:
            break

    while len(extracted_links) < 400:
      try:
        link_element = driver.find_element(By.CSS_SELECTOR, 'div.row div.col-lg-8.offset-lg-2.col-12 div.d-grid.gap-2.mt-2.mb-4 button.btn.btn-lg.ButtonBG')

        try:
          # Click on the anchor element
          link_element.click()
          #load_more_element.click()
          time.sleep(3)  # Wait for new content to load
          scroll()

          # Get the updated page source
          page_source = driver.page_source
          soup = BeautifulSoup(page_source, 'html.parser')
          # Find all links within the <div class="stories-set gqNK1"> snippet again
          links_within_div = soup.select('div.row.read-more-container div.col-lg-12.col-12.countclass div.DCatNewsList3 a[href]')
          #print(links_within_div)
          # Add newly loaded unique links to the extracted_links set
          for link in links_within_div:
              extracted_links.add(link['href'])
              #print(len(extracted_links))
              if len(extracted_links) >= 400:
                  break
        except ElementClickInterceptedException:
          print("Element is not clickable. Exiting loop.")
          break
      except NoSuchElementException:
          print("No more load_more_element found. Exiting loop.")
          break

    return extracted_links

# for link in matching_links:
#     url = link['href']
url = "https://www.dailyjanakantha.com/different-news/"
extracted_links = extract_links(url)
all_extracted_links.update(extracted_links)

#Convert the set to a list before printing
all_extracted_links = list(all_extracted_links)
print(all_extracted_links)
print(len(all_extracted_links))

# Close the web driver
#driver.quit()

Element is not clickable. Exiting loop.
['https://www.dailyjanakantha.com/different-news/news/708548', 'https://www.dailyjanakantha.com/different-news/news/712777', 'https://www.dailyjanakantha.com/different-news/news/713246', 'https://www.dailyjanakantha.com/different-news/news/704653', 'https://www.dailyjanakantha.com/different-news/news/706671', 'https://www.dailyjanakantha.com/different-news/news/710548', 'https://www.dailyjanakantha.com/different-news/news/703148', 'https://www.dailyjanakantha.com/different-news/news/704668', 'https://www.dailyjanakantha.com/different-news/news/706554', 'https://www.dailyjanakantha.com/different-news/news/707896', 'https://www.dailyjanakantha.com/different-news/news/712849', 'https://www.dailyjanakantha.com/different-news/news/711782', 'https://www.dailyjanakantha.com/different-news/news/707964', 'https://www.dailyjanakantha.com/different-news/news/707394', 'https://www.dailyjanakantha.com/different-news/news/704841', 'https://www.dailyjanakantha.

In [ ]:
import re
extracted_data = []
visited_links = set()

for href in all_extracted_links:
    if href not in visited_links:
        visited_links.add(href)
        driver.get(href)  # Visit the link
        wait = WebDriverWait(driver, 10)
        time.sleep(3)  # Wait for the page to load
        scroll()
        time.sleep(3)

        page_source = driver.page_source
        soup = BeautifulSoup(page_source, 'html.parser')

        # Extract title and article content
        title_element = soup.find('div', class_='DDetailsTitle')
        if title_element:
            title = title_element.find('h1').text.strip()
            print('Title:', title)
        else:
            print('Title element not found')

        paragraphs = soup.find_all('div', attrs={'id': 'contentDetails'})
        article = ''
        for p in paragraphs:
            p_tags = p.find_all('p')
            for tag in p_tags:
                article += tag.get_text(strip=True) + ' '
        article = article.replace("This is a modal window. Beginning of dialog window. Escape will cancel and close the window. End of dialog window.", " ")
        print(article)

        extracted_data.append({'link': href, 'summary': title, 'article': article})
        print(len(extracted_data))

Title: ঝুঁকি নিয়ে প্রতিদিন হাজারো শ্রমিকের সড়ক পারাপার
নারায়ণগঞ্জেরসিদ্ধিরগঞ্জেরআদমজীইপিজেডেরপ্রধানফটকেরসামনেফুটওভারব্রিজনাথাকায়প্রতিদিনহাজারহাজারশ্রমিকজীবনেরঝুঁকিনিয়েব্যস্ততমনারায়ণগঞ্জ-আদমজী-শিমরাইলসড়কটিপারহচ্ছেন।এস্থানেএকটিফুটওভারব্রিজনাথাকায়ব্যস্ততমসড়কটিপারহতেগিয়েসড়কদুর্ঘটনায়শ্রমিকরাহতাহতহচ্ছেন।অন্যদিকেইপিজেডেরঅভ্যন্তরেকারখানাগুলোতেপ্রবেশওছুটিরসময়হাজারহাজারশ্রমিকরাস্তাপারাপারহওয়ায়তীব্রযানজটওমানবজটেরসৃষ্টিহচ্ছে।এতেএসড়কেচলাচলরতযাত্রীওস্থানীয়দেরচরমদুর্ভোগপোহাতেবাধ্যহচ্ছেন।জরুরিভিত্তিতেআদমজীইপিজেডেরপ্রধানফটকেরসামনেএকটিফুটওভারব্রিজনির্মাণেরজোরদাবিজানিয়েছেনশ্রমিক-কর্মচারীওস্থানীয়রা।   জানাযায়,অধুনালুপ্তআদমজীপাটকলেরজায়গায়২০০৬সালে২৯২দশমিক৬২একরজাগয়ারওপরগড়েউঠেছেআদমজীইপিজেড।এইপিজডেটিনারায়ণগঞ্জ-আদমজী-শিমরাইল(নারায়ণঞ্জ-আদমজী-ডেমরা)সড়কেরপাশেইঅবস্থিত।এসড়কদিয়েইইপিজেডেরপোশাককারখানাসহবিভিন্নশিল্পপ্রতিষ্ঠানেযাতায়াতকরতেহচ্ছে।আদমজীইপিজেডে২৭৩টিশিল্পপ্লটরয়েছে। এইপিজেডেদেশী-বিদেশীশ্রমিকসহপ্রায়৬০হাজারশ্রমিক-কর্মচারীওকর্মকর্তাকাজকরছে।প্রতিদিনপ্রায়৬০হাজারশ্রমিকএইপিজেডেরবিভিন্নপোশাকসহবিভিন্নকারখানায়আসা-যাওয়াক

# **Jaijaidin**

In [ ]:
# all_links = soup.find_all('a', href=True)
# all_links
specific_element = soup.find('div', class_='d-flex justify-content-between')
matching_links = specific_element.find_all('a')

# Print the extracted <a> tags
for a_tag in matching_links:
    print(a_tag)

<a href="https://www.jaijaidinbd.com"><i class="fa-solid fa-house" style="display: none;"></i><img alt="logo" class="main-logo img-fluid" src="https://www.jaijaidinbd.com/templates/web-view/images/logo_new.png" style="display: inline-block;"/></a>
<a href="https://www.jaijaidinbd.com/national">জাতীয়</a>
<a href="https://www.jaijaidinbd.com/wholecountry">সারাদেশ</a>
<a href="https://www.jaijaidinbd.com/politics">রাজনীতি</a>
<a href="https://www.jaijaidinbd.com/international">আন্তর্জাতিক</a>
<a href="https://www.jaijaidinbd.com/sports">খেলাধুলা</a>
<a href="https://www.jaijaidinbd.com/economics">অর্থনীতি</a>
<a href="https://www.jaijaidinbd.com/entertainment">বিনোদন</a>
<a href="https://www.jaijaidinbd.com/information-technology">তথ্য প্রযুক্তি</a>
<a href="https://www.jaijaidinbd.com/islam-and-religion">ইসলাম ও ধর্ম</a>
<a class="text-danger" href="/video-gallery">ভিডিও</a>
<a href="/todays-paper">
                    আজকের যায়যায়দিন </a>
<a href="https://www.ejjdin.com/" target="_blan

In [ ]:
all_extracted_links = set()

def extract_links(url):
    extracted_links = set()
    driver.get(url)  # Load the URL in the browser
    wait = WebDriverWait(driver, 10)
    time.sleep(3)  # Wait for the page to load

    # Scroll the page to load dynamic content
    scroll()

    # Get the initial page source
    page_source = driver.page_source

    # Parse the initial page content
    soup = BeautifulSoup(page_source, 'html.parser')

    # Find all links within the <div> elements with either class 'stories-set gqNK1' or 'stories-set _9rLDm'
    links_within_div = soup.select('div.row.my-3 div.sub-news a[href]')
    #print(len(links_within_div))

    # Add each unique link to the extracted_links set
    for link in links_within_div:
        extracted_links.add(link['href'])
        if len(extracted_links) >= 400:
            break

    prev_links_count = 0
    while len(extracted_links) < 400:
      try:
        link_element = driver.find_element(By.CSS_SELECTOR, 'div.text-center.my-3 a#find_more')

        try:
          # Click on the anchor element
          driver.execute_script("arguments[0].click();", link_element)
          #load_more_element.click()
          time.sleep(3)  # Wait for new content to load
          scroll()

          # Get the updated page source
          page_source = driver.page_source
          soup = BeautifulSoup(page_source, 'html.parser')
          # Find all links within the <div class="stories-set gqNK1"> snippet again
          links_within_div = soup.select('div.row.my-3 div.sub-news a[href]')
          #print(len(links_within_div))
          new_links_count = len(links_within_div)
          print("New links found:", new_links_count)
          # Add newly loaded unique links to the extracted_links set
          for link in links_within_div:
              extracted_links.add(link['href'])
              #print(len(extracted_links))
          if new_links_count == prev_links_count:
              print("No more links found. Exiting loop.")
              break
          prev_links_count = new_links_count
          if len(extracted_links) >= 400:
                  break

        except ElementClickInterceptedException:
          print("Element is not clickable. Exiting loop.")
          break
        except ElementNotInteractableException:
          # Handle ElementNotInteractableException
          print("Element not interactable.")
          break
      except NoSuchElementException:
          print("No more load_more_element found. Exiting loop.")
          break

    return extracted_links

# for link in matching_links:
#     url = link['href']
url = "https://www.jaijaidinbd.com/islam-and-religion"
extracted_links = extract_links(url)
all_extracted_links.update(extracted_links)

#Convert the set to a list before printing
all_extracted_links = list(all_extracted_links)
print(all_extracted_links)
print(len(all_extracted_links))

# Close the web driver
#driver.quit()

New links found: 9
New links found: 14
New links found: 19
New links found: 24
New links found: 29
New links found: 34
New links found: 39
New links found: 44
New links found: 49
New links found: 59
New links found: 64
New links found: 69
New links found: 74
New links found: 79
New links found: 84
New links found: 89
New links found: 94
New links found: 99
New links found: 104
New links found: 109
New links found: 114
New links found: 119
New links found: 124
New links found: 129
New links found: 134
New links found: 139
New links found: 144
New links found: 149
New links found: 154
New links found: 159
New links found: 164
New links found: 169
New links found: 174
New links found: 179
New links found: 184
New links found: 189
New links found: 194
New links found: 199
New links found: 204
New links found: 209
New links found: 214
New links found: 219
New links found: 224
New links found: 229
New links found: 234
New links found: 239
New links found: 244
New links found: 249
New links f

In [ ]:
import re
extracted_data = []
visited_links = set()

for href in all_extracted_links:
    if href not in visited_links:
        visited_links.add(href)
        driver.get(href)  # Visit the link
        wait = WebDriverWait(driver, 10)
        time.sleep(3)  # Wait for the page to load
        scroll()
        time.sleep(3)

        page_source = driver.page_source
        soup = BeautifulSoup(page_source, 'html.parser')

        # Extract title and article content
        title_element = soup.find('h2', class_='details-title font-weight-bold')
        if title_element:
            title = title_element.text.strip()
            print('Title:', title)
        else:
            print('Title element not found')

        paragraphs = soup.find_all('div', class_='dtl_content_section')
        article = ''
        for p in paragraphs:
            p_tags = p.find_all('p')
            for tag in p_tags:
                article += tag.get_text(strip=True) + ' '
        #article = article.replace("This is a modal window. Beginning of dialog window. Escape will cancel and close the window. End of dialog window.", " ")
        print(article)

        extracted_data.append({'link': href, 'summary': title, 'article': article})
        print(len(extracted_data))

Title: রোজা আল্লাহর ভালোবাসার অন্যতম নিদর্শন
রোজা দেহ-আত্মার সুস্থতার কারণ। রোজা মানুষের জন্য এক রুহানি খাদ্য, যা পরকালে মানুষের জন্য খাদ্যের কাজ দেবে। সর্বোপরি রোজা আল্লাহর ভালোবাসার অন্যতম নিদর্শন। পবিত্র রমজান মানুষকে আত্মশুদ্ধি ও পুণ্য অর্জনের এক অবারিত সুযোগ এনে দেয়; যেখানে একটি নফল ইবাদত অন্য মাসের ফরজ ইবাদতের এবং রমজানের একটি ফরজ ইবাদত অন্য মাসের ৭০টি ফরজ ইবাদতের সমপর্যায়ের গুরুত্ব বহন করে থাকে। তাই স্বাভাবিকভাবেই পবিত্র রমজান মাস মানুষের জীবনে সংশোধন লাভ ও অগণিত সওয়াবের বার্তা নিয়ে তার শুভাগমন ঘটায়। মানুষের উচিত হলো এমন পুণ্যময় ও বরকতের মাসকে সর্বোচ্চ মূল্যায়ন করা এবং বৈচিত্র্যপূর্ণ ইবাদতের মাধ্যমে ইহকালীন কল্যাণ অর্জন ও পারলৌকিক প্রত্যাশিত সাফল্যের সবটুকু লাভে আত্মনিয়োগ করা। রমজান এলে মুসলমানদের হৃদয়ে জাগে পবিত্র শিহরণ। চার দিকে সৃষ্টি হয় স্বর্গীয় আবহ। পবিত্র রমজানে একজন রোজাদার শুধু পানাহার বর্জনেই সন্তুষ্ট থাকেন না; বরং সবরকম কটু কথা, মন্দ কাজ ও যাবতীয় অনাচার থেকে নিজেকে বিরত রাখেন। এর মধ্য দিয়ে তিনি সারা বছরের জন্য এক সুশৃঙ্খল প্রশিক্ষণ নিয়ে থাকেন এবং রোজার সেই অনুপম শিক্

# **Mains**

In [ ]:
# def common_elements(list1, list2):
#     set1 = set(list1)
#     set2 = set(list2)
#     common = set1.intersection(set2)
#     return len(list(common)) if common else "No common elements"
# result = common_elements(all_extracted_links, temp)
# print(result)

No common elements


In [ ]:
import pandas as pd
extracted_data = pd.DataFrame(extracted_data)
print(len(extracted_data))

295


In [ ]:
# # Create a mask for rows where 'summary' contains the specified substring
# contains_substring_mask = (extracted_data['summary'].str.contains('শুভ জন্মদিন')) | (extracted_data['summary'].str.contains('কারিনার অদেখা ৫ রূপ')) | (extracted_data['summary'].str.contains('স্টার অব দ্য উইক : পূজা চেরী'))

# # Count the number of rows to be removed
# rows_to_remove = contains_substring_mask.sum()

# # Remove rows that meet the condition
# extracted_data = extracted_data[~contains_substring_mask]

# # Print the total number of rows removed
# print("Total number of rows removed:", rows_to_remove)

Total number of rows removed: 30


In [ ]:
# Check if 'article' column contains empty string or '|'
empty_article_mask = (extracted_data['article'] == '') | (extracted_data['article'].str.strip() == '।')

# Check if 'title' column contains 'Title Not Found'
no_title_mask = (extracted_data['summary'] == 'Title Not Found') | (extracted_data['summary'] == 'Title element not found')

# Combine the masks using logical OR
remove_rows_mask = empty_article_mask | no_title_mask

# Count the number of rows to be removed
rows_to_remove = remove_rows_mask.sum()

# Remove rows that meet the conditions
extracted_data = extracted_data[~remove_rows_mask]

# Print the total number of rows removed
print("Total number of rows removed:", rows_to_remove)
print("updated length of extracted_data:", len(extracted_data))
extracted_data.to_csv('extracted_data.csv')

Total number of rows removed: 0
updated length of extracted_data: 295


In [ ]:
import pandas as pd
try:
    final_df = pd.read_csv('/content/drive/MyDrive/BanglaNewsSumary/BanglaNewsSummary.csv', index_col=0)
except FileNotFoundError:
    final_df = pd.DataFrame(columns=['link', 'summary', 'article'])
print(len(final_df))

21472


In [ ]:
final_df = pd.concat([final_df, extracted_data], ignore_index=True)
print(len(final_df))

21767


In [ ]:
#final_df.to_csv('BanglaNewsSummary.csv')
final_df.to_csv('/content/drive/MyDrive/BanglaNewsSumary/BanglaNewsSummary.csv')